## Imports

In [1]:
import torch
if torch.cuda.is_available():
    print("GPU is available")
else:
    print("GPU is not available")

GPU is available


In [2]:
from bertopic import BERTopic
import pandas as pd
from umap import UMAP
from hdbscan import HDBSCAN
from bertopic.representation import KeyBERTInspired, OpenAI
from bertopic.dimensionality import BaseDimensionalityReduction


from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer

import nltk
nltk.download('stopwords')
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords

from octis.evaluation_metrics.coherence_metrics import Coherence
from octis.evaluation_metrics.diversity_metrics import TopicDiversity

from tqdm import tqdm

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\wanjanss\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


## OpenAI API access & prompt templates

In [3]:
import openai
client = openai.OpenAI()

completion = client.chat.completions.create(
    model="gpt-4o-mini",
    messages=[
        {"role": "system", "content": "You are a helpful assistant."},
        {
            "role": "user",
            "content": "Write a haiku about recursion in programming."
        }
    ]
)

print(completion.choices[0].message)

ChatCompletionMessage(content='Function calls itself,  \nInfinite depths intertwine,  \nLogic’s dance unfolds.', refusal=None, role='assistant', audio=None, function_call=None, tool_calls=None, annotations=[])


In [4]:
system_prompt = """" 
You are a helpful assistant tasked with identifying overlapping topics.
"""

instruction_prompt = """
Below I will provide a numbered list of topics. Each line represents the topic words of a topic. Return the index of the two most similar topics in python list format.
[TOPICS]

Return only the python list and nothing more!
"""

demonstration_prompt = """
Below I will provide a numbered list of topic words. Each line represents the topic words of a topic. Return the index of the two most similar topics in python list format.

0: astronaut, rocket, planet, galaxy, NASA, telescope, satellite, mission, orbit, cosmos
1: apple, fruit, red, sweet, tree, orchard, juicy, vitamin, snack, fresh
2: computer, laptop, technology, device, screen, keyboard, processor, portable, battery, software
3: orange, fruit, citrus, vitamin, juicy, tropical, snack, fresh, tree, peel
4: car, vehicle, engine, road, drive, wheels, speed, travel, gasoline, transportation
5: book, library, read, pages, author, fiction, genre, chapter, knowledge, cover

Return only the python list and nothing more!
"""

demonstration_answer = """
[1, 3]
"""

In [5]:
instruction_prompt_labeled = """
Below I will provide a numbered list of topics. Each line represents a topic. Return the index of the two most similar topics in python list format.
[TOPICS]

Return only the python list and nothing more!
"""

demonstration_prompt_labeled = """
Below I will provide a numbered list of topics. Each line represents a topic. Return the index of the two most similar topics in python list format.

1: Space Exploration
2: Artificial Intelligence in Industry
3: Ocean Conservation
4: Medieval History
5: AI applied in Industry

Return only the python list and nothing more!
"""

demonstration_answer_labeled = """
[2, 5]
"""

## Functions

In [6]:
def get_topic_words(topic_model, representation = "Representation"):
  all_topic_words = topic_model.get_topic_info()[representation]
  topic_words = []
  for words in all_topic_words:
    topic_words.append(words)

  # remove first entry (topic -1)
  topic_words = topic_words[1:]
  return topic_words

In [7]:
def clean_topic_words(topic_words):
    return [topic for topic in topic_words if topic and all(word for word in topic)]

In [8]:
#function to evaluate topic coherence and diversity of topic model output
def evaluate_bertopic(topic_words, tokenized_docs):
  print(f"Length topic words before cleaning: {len(topic_words)}")
  topic_words = clean_topic_words(topic_words)
  print(f"Length topic words after cleaning: {len(topic_words)}")

  print(topic_words)
  topic_words_dict = {'topics': topic_words}
  print(topic_words_dict)


  c_npmi = Coherence(topk=10, texts=tokenized_docs)
  diversity = TopicDiversity(topk=10)
  topic_coherence_score = round(c_npmi.score(topic_words_dict), 4)
  topic_diversity_score = round(diversity.score(topic_words_dict), 4)

  print(f"Topic coherence score (NPMI) {topic_coherence_score}")
  print(f"Topic diversity score {topic_diversity_score}")
  return (topic_coherence_score + topic_diversity_score)/2

In [9]:
def merge_topics_llm(topic_model, reduced_nr, representation="Representation"):

    nr_of_topics = len(topic_model.topic_sizes_) - 1

    while nr_of_topics > reduced_nr:
        to_replace = ""
        i = 0
        topic_words =  get_topic_words(topic_model, representation)
        for words in topic_words:
            joined_words = ", ".join(words)
            to_replace += f"{i}: {joined_words}\n"
            i+=1

        real_instruction_prompt = instruction_prompt.replace('[TOPICS]', to_replace)

        if representation == "OpenAI":
            real_instruction_prompt = instruction_prompt_labeled.replace('[TOPICS]', to_replace)
            messages=[
                {"role":"system", "content": system_prompt},
                {"role": "user", "content": demonstration_prompt_labeled},
                {"role": "assistant", "content": demonstration_answer_labeled},
                {"role":"user", "content": real_instruction_prompt}    
                    ]
            
        else:
            messages=[
                {"role":"system", "content": system_prompt},
                {"role": "user", "content": demonstration_prompt},
                {"role": "assistant", "content": demonstration_answer},
                {"role":"user", "content": real_instruction_prompt}    
                    ]
        
        print(real_instruction_prompt)


        response = client.chat.completions.create(
            model="gpt-4o-mini",
            messages=messages
            )

        response_string = response.choices[0].message.content
        print(response_string)

        merge_list = eval(response_string)
        topic_model.merge_topics(docs, merge_list)
        nr_of_topics = len(topic_model.topic_sizes_) - 1


In [20]:
def merge_label_embeddings(topic_model, embedding_model, docs, nr_topics, representation, use_ctfidf=False):
    topic_labels = topic_model.get_topic_info()[representation]
    print(topic_labels)
    if representation == "OpenAI":
        flattened_labels = [item for sublist in topic_labels for item in sublist]
        print(len(flattened_labels))
        topic_model.topic_embeddings_ = embedding_model.encode(flattened_labels)
        topic_model.reduce_topics(docs, nr_topics, use_ctfidf)
    else:
        topic_model.topic_embeddings_ = embedding_model.encode(topic_labels)
        topic_model.reduce_topics(docs, nr_topics, use_ctfidf)

## Read in data

In [10]:
basetable_path = "./data/realdonaldtrump.csv"
basetable = pd.read_csv(basetable_path)
basetable.head()

id                                               link  \
0  1698308935  https://twitter.com/realDonaldTrump/status/169...   
1  1701461182  https://twitter.com/realDonaldTrump/status/170...   
2  1737479987  https://twitter.com/realDonaldTrump/status/173...   
3  1741160716  https://twitter.com/realDonaldTrump/status/174...   
4  1773561338  https://twitter.com/realDonaldTrump/status/177...   

                                             content                 date  \
0  Be sure to tune in and watch Donald Trump on L...  2009-05-04 13:54:25   
1  Donald Trump will be appearing on The View tom...  2009-05-04 20:00:10   
2  Donald Trump reads Top Ten Financial Tips on L...  2009-05-08 08:38:08   
3  New Blog Post: Celebrity Apprentice Finale and...  2009-05-08 15:40:15   
4  "My persona will never be that of a wallflower...  2009-05-12 09:07:28   

   retweets  favorites mentions hashtags  
0       510        917      NaN      NaN  
1        34        267      NaN      NaN  
2        13         19      NaN      NaN  
3        11         26      NaN      NaN  
4      1375       1945      NaN      NaN

In [11]:
%%time
# Select the 'full_text' column for the random subsample of rows
docs = basetable.loc[:, 'content'].tolist()

print(len(docs))

# split the docs into tokens, this is necessary for the coherence and diversity evaluation later
tokenized_docs = docs.copy()
tokenizer = RegexpTokenizer(r'\w+')
STOPWORDS = stopwords.words('english')
for idx in tqdm(range(len(tokenized_docs)), desc="Tokenizing Documents"):
    # Convert to lowercase and split into words
    tokenized_docs[idx] = tokenized_docs[idx].lower()
    tokenized_docs[idx] = tokenizer.tokenize(tokenized_docs[idx])

    # Remove stopwords & numbers
    tokenized_docs[idx] = [token for token in tokenized_docs[idx] if token not in STOPWORDS and not token.isnumeric()]

    # Remove words that are only one character
    tokenized_docs[idx] = [token for token in tokenized_docs[idx] if len(token) > 1]

43352


Tokenizing Documents: 100%|██████████| 43352/43352 [00:02<00:00, 16807.64it/s]

CPU times: total: 2.41 s
Wall time: 2.59 s


In [12]:
texts= docs
# Calculate the total number of characters and words across all texts
total_characters = sum(len(text) for text in texts)
total_words = sum(len(text.split()) for text in texts)

# Calculate the average length of characters and words per text
average_characters = total_characters / len(texts)
average_words = total_words / len(texts)

# Print the average character and word length per text
print(f"Average length of all texts: {average_characters:.2f} characters")
print(f"Average number of words in all texts: {average_words:.2f} words")

Average length of all texts: 131.53 characters
Average number of words in all texts: 20.76 words


## Embed and reduce documents, define modules,  and train initial BERTopic model

In [13]:
# Embed the docs and reduce the dimensionality using UMAP upfront to speed up the process when training the BERTopic model repeatedly
embedding_model = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = embedding_model.encode(docs, show_progress_bar=True)
reduced_embeddings = UMAP(n_neighbors=15, n_components=5, min_dist=0.0, metric='cosine', verbose=True, random_state=42).fit_transform(embeddings)

Batches:   0%|          | 0/1355 [00:00<?, ?it/s]

UMAP(angular_rp_forest=True, metric='cosine', min_dist=0.0, n_components=5, n_jobs=1, random_state=42, verbose=True)
Mon Jul 28 14:47:34 2025 Construct fuzzy simplicial set
Mon Jul 28 14:47:35 2025 Finding Nearest Neighbors
Mon Jul 28 14:47:35 2025 Building RP forest with 15 trees
Mon Jul 28 14:47:42 2025 NN descent for 15 iterations
	 1  /  15
	 2  /  15
	 3  /  15
	 4  /  15
	 5  /  15
	 6  /  15
	 7  /  15
	Stopping threshold met -- exiting after 7 iterations
Mon Jul 28 14:48:03 2025 Finished Nearest Neighbor Search
Mon Jul 28 14:48:06 2025 Construct embedding


Epochs completed:   0%|            0/200 [00:00]

	completed  0  /  200 epochs
	completed  20  /  200 epochs
	completed  40  /  200 epochs
	completed  60  /  200 epochs
	completed  80  /  200 epochs
	completed  100  /  200 epochs
	completed  120  /  200 epochs
	completed  140  /  200 epochs
	completed  160  /  200 epochs
	completed  180  /  200 epochs
Mon Jul 28 14:48:35 2025 Finished embedding


In [14]:
%%time
# define modules
empty_dimensionality_model = BaseDimensionalityReduction() #define empty dimensionality reduction model for faster re-training
hdbscan_model = HDBSCAN(min_cluster_size=100, metric='euclidean', cluster_selection_method='eom', prediction_data=True)
vectorizer_model = CountVectorizer(stop_words="english", min_df=1, ngram_range=(1, 1))

representation_model = {
    "KeyBERT": KeyBERTInspired(),
    "OpenAI": OpenAI(client,  model="gpt-4o-mini", chat=True)
}

CPU times: total: 0 ns
Wall time: 0 ns


In [22]:
%%time
# training
topic_model = BERTopic(

  # Pipeline models
  embedding_model=embedding_model,
  umap_model=empty_dimensionality_model,
  hdbscan_model=hdbscan_model,
  vectorizer_model=vectorizer_model,
  representation_model=representation_model,

  # Hyperparameters
  top_n_words=10,
  verbose=True
  # nr_topics='auto'
)

topics, probs = topic_model.fit_transform(docs, reduced_embeddings)

2025-07-28 14:54:19,615 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2025-07-28 14:54:19,617 - BERTopic - Dimensionality - Completed ✓
2025-07-28 14:54:19,620 - BERTopic - Cluster - Start clustering the reduced embeddings
2025-07-28 14:54:21,962 - BERTopic - Cluster - Completed ✓
2025-07-28 14:54:21,977 - BERTopic - Representation - Extracting topics from clusters using representation models.
100%|██████████| 49/49 [00:43<00:00,  1.13it/s]
2025-07-28 14:55:08,493 - BERTopic - Representation - Completed ✓


CPU times: total: 6.52 s
Wall time: 49.3 s


In [16]:
#scoring before
topic_words = get_topic_words(topic_model, "Representation")
score = evaluate_bertopic(topic_words, tokenized_docs)
print(f"Overall score: {score}")

Length topic words before cleaning: 48
Length topic words after cleaning: 48
[['realdonaldtrump', 'run', 'president', 'trump', 'donald', 'mr', 'trump2016', 'need', '2016', 'vote'], ['hillary', 'clinton', 'democrats', 'crooked', 'hunt', 'witch', 'fbi', 'collusion', 'russia', 'mueller'], ['thanks', 'true', 'thank', 'luck', 'good', 'great', 'yes', 'nice', 'hi', 'billmaher'], ['entrepreneurs', 'think', 'success', 'focus', 'big', 'work', 'don', 'champion', 'like', 'midas'], ['com', 'twitter', 'thank', 'makeamericagreatagain', 'www', 'pic', 'https', 'crowd', 'join', 'donaldjtrump'], ['fake', 'news', 'media', 'cnn', 'failing', 'ratings', 'nytimes', 'dishonest', 'story', 'bad'], ['golf', 'course', 'doral', 'scotland', 'trump', 'turnberry', 'club', 'http', 'trumpdoral', 'national'], ['border', 'wall', 'mexico', 'immigration', 'security', 'southern', 'democrats', 'illegal', 'country', 'laws'], ['hotel', 'chicago', 'tower', 'trump', 'trumpchicago', 'building', 'http', 'sign', 'realdonaldtrump', '

## Topic reduction

In [17]:
'''
This code applies agglomerative clustering to reduce the number of topics in the BERTopic model. 
To use the c-TF-IDF representation, set use_ctfidf=True.
To use the average SBERT topic embedding representation, set use_ctfidf=False.
'''

topic_model.reduce_topics(docs, nr_topics=26, use_ctfidf=True)

2025-07-28 14:50:57,548 - BERTopic - Topic reduction - Reducing number of topics
100%|██████████| 26/26 [00:24<00:00,  1.08it/s]
2025-07-28 14:51:23,710 - BERTopic - Topic reduction - Reduced number of topics from 49 to 26


In [21]:
'''
This code applies agglomerative clustering to reduce the number of topics in the BERTopic model using the SBERT embeddings of the (LLM-generated) topic labels.
To use the top-10 words representation, set representation="Representation".
To use the LLM-generated topic labels, set representation="OpenAI".
use_ctfidf should be left as False
'''

merge_label_embeddings(topic_model, embedding_model, docs, 26, "OpenAI", use_ctfidf=False)

2025-07-28 14:53:31,217 - BERTopic - Topic reduction - Reducing number of topics


0                   [Trump Rally and Campaign Messages]
1                      [Support for Trump as President]
2     [Trump-Russia Investigation and Accusations Ag...
3                       [Thanks and Good Luck Messages]
4          [Empowering Young Entrepreneurs for Success]
5     [Trump Rally Announcements and Voting Encourag...
6                      [Fake News and Media Corruption]
7                       [Best Golf Courses in Scotland]
8     [U.S. Southern Border Security and Immigration...
9            [Trump Hotels Overview in Chicago and NYC]
10        [Support for Veterans and Emergency Response]
11          [China Trade Deals and Tariff Negotiations]
12       [Twitter Praise and Thanks for Public Figures]
13                       [Sports and Teams Discussions]
14            [Obamacare Repeal and Replacement Debate]
15       [Political Endorsements for Strong Candidates]
16    [Positive Economic Performance and Stock Marke...
17                        [CelebApprentice Discu

100%|██████████| 26/26 [00:20<00:00,  1.27it/s]
2025-07-28 14:53:53,605 - BERTopic - Topic reduction - Reduced number of topics from 49 to 26


In [23]:
'''
This code applies agglomerative clustering to reduce the number of topics using the LLM-prompting method. 
To use the top-10 words representation, set representation="Representation".
To use the LLM-generated topic labels, set representation="OpenAI".
'''

merge_topics_llm(topic_model, 25, "OpenAI")


Below I will provide a numbered list of topics. Each line represents a topic. Return the index of the two most similar topics in python list format.
0: Support for Trump as President
1: Trump-Russia Investigation and Democratic Allegations
2: Gratitude and Good Luck Wishes
3: Empowering Young Entrepreneurs for Success
4: Trump Rally Announcements
5: Fake News and Media Criticism
6: Best Golf Courses in Scotland and Trump International Golf Links
7: Border Security and Immigration Reform
8: Luxury Hotels and Restaurants in Chicago and NYC
9: Support for Veterans and Disaster Response
10: China Trade and Tariffs Negotiations
11: Twitter Celebrations and Honorary Mentions
12: Sports and Events Discussion
13: Repeal and Replace Obamacare
14: Political Endorsements and Support for Candidates
15: Economic Growth and Stock Market Success
16: Celeb Apprentice Discussion
17: Twitter Image Links
18: Criticism of Barack Obama and His Presidency
19: Book Recommendations and Authors
20: Donald Tru

100%|██████████| 48/48 [00:35<00:00,  1.36it/s]



Below I will provide a numbered list of topics. Each line represents a topic. Return the index of the two most similar topics in python list format.
0: Trump 2016 Presidential Campaign and Hillary Clinton's Defeat
1: Good Luck Wishes
2: Entrepreneurial Mindset for Success
3: Trump Rally Announcements and Thank Yous
4: Fake News and Media Criticism
5: Trump International Golf Courses and Awards in Scotland
6: Border Security and Immigration Policy
7: Trump Hotels and Luxury Accommodations
8: Support for Disaster Response and Victims
9: US-China Trade Relations and Negotiations
10: Trump Support and Gratitude on Twitter
11: Yankees and Derek Jeter in Baseball
12: Repeal and Replace Obamacare Debate
13: Political Endorsements for Strong Candidates
14: Economic Optimism and Stock Market Performance
15: Celeb Apprentice Discussion
16: Twitter Images and Links
17: Criticism of Barack Obama and His Administration
18: Books by Donald Trump and Authors on America
19: Trump Signature Collection

100%|██████████| 47/47 [00:35<00:00,  1.33it/s]



Below I will provide a numbered list of topics. Each line represents a topic. Return the index of the two most similar topics in python list format.
0: Trump-Russia Controversy and 2016 Election Dynamics
1: Gratitude and Good Wishes
2: Entrepreneurial Mindset and Success Principles
3: Trump Campaign Rallies
4: Fake News and Media Criticism
5: Trump International Golf Courses in Scotland
6: Border Security and Immigration Policy Debate
7: Trump Hotel Properties and Luxury Experiences
8: Disaster Response and Support
9: China-U.S. Trade Negotiations and Tariffs
10: Praise for Charlie Kirk and Team Trump
11: Yankees and Derek Jeter's performance
12: Obamacare Repeal and Replacement Debate
13: Political Endorsements for Strong Candidates
14: Economic Performance and Stock Market Growth
15: CelebApprentice Boardroom Reactions
16: Twitter Images
17: Obama's Loyalty and Campaigning Issues
18: Books by Influential Authors and Trump
19: Trump Signature Collection at Macy's
20: Trump Polling Le

...

100%|██████████| 28/28 [00:21<00:00,  1.30it/s]



Below I will provide a numbered list of topics. Each line represents a topic. Return the index of the two most similar topics in python list format.
0: Trump Support and Hillary Criticism
1: Business Success and Entrepreneurial Mindset
2: Border Security and Immigration Policy
3: Support for First Responders and Victims During Hurricanes
4: U.S.-China Trade Relations and Tariffs
5: Yankees and Derek Jeter's Performance
6: Obamacare Premiums and Repeal Efforts
7: Positive Economic Outlook and Stock Market Growth
8: Twitter Images Sharing
9: Fox News Interviews Tonight
10: Opposition to Wind Turbines in Scotland
11: Iran's Nuclear Threat and Diplomatic Tensions
12: Syria and ISIS Military Policy
13: Prime Minister Welcome Messages
14: North Korea-US Relations and Denuclearization Efforts
15: Keystone Pipeline and Oil Prices
16: Mitt Romney's Presidential Campaign
17: Miss Universe Pageant 2012
18: Coronavirus Response and Testing
19: National Debt and Barack Obama
20: Tax Cuts and Refor

100%|██████████| 27/27 [00:20<00:00,  1.30it/s]



Below I will provide a numbered list of topics. Each line represents a topic. Return the index of the two most similar topics in python list format.
0: Trump Support and Impeachment Discussion
1: Border Security and Immigration Policy Debate
2: Support for First Responders and Veterans During Disasters
3: U.S.-China Trade Relations and Tariffs
4: Yankees and NFL Discussion
5: Repeal and Replace ObamaCare
6: Economic Growth and Stock Market Records
7: Twitter Media Links
8: Fox News Interviews Tonight
9: Opposition to Alex Salmond's Wind Turbines in Scotland
10: Iran Nuclear Weapons and Sanctions Debate
11: U.S. Military Role in Syria and ISIS Defeat
12: International Prime Minister Meetings
13: North Korea Diplomatic Relations and Denuclearization Efforts
14: Oil Prices and the Keystone XL Pipeline Debate
15: Mitt Romney's Presidential Campaign and Debate Performance
16: Miss Universe Pageant 2012
17: Federal Government Response to Coronavirus Pandemic
18: National Debt Under Barack O

100%|██████████| 26/26 [00:18<00:00,  1.41it/s]


In [24]:
#scoring after
topic_words = get_topic_words(topic_model, "Representation")
score = evaluate_bertopic(topic_words, tokenized_docs)
print(f"Overall score: {score}")

Length topic words before cleaning: 25
Length topic words after cleaning: 25
[['realdonaldtrump', 'trump', 'com', 'great', 'thanks', 'twitter', 'thank', 'president', 'https', 'http'], ['border', 'wall', 'mexico', 'immigration', 'security', 'democrats', 'southern', 'illegal', 'country', 'laws'], ['honor', 'twitter', 'pic', 'prayers', 'today', 'com', 'hurricane', 'great', 'families', 'fema'], ['china', 'trade', 'tariffs', 'chinese', 'deal', 'farmers', 'http', 'countries', 'currency', 'dollars'], ['yankees', 'nfl', 'rod', 'nflcommish', 'game', 'derek', 'great', 'bills', 'players', 'anthem'], ['economy', 'jobs', 'market', 'unemployment', 'stock', 'numbers', 'record', 'high', '000', 'economic'], ['pic', 'twitter', 'com', 'z0i7wbsgtp', 'gizwksbuus', 'p5imhmjqs1', 'dnfxkc8uug', '9jgdue5bf8', 'jds4zuxxjg', 'knvqf6jdil'], ['interviewed', '00', 'enjoy', 'tonight', 'foxnews', 'interview', '10', 'seanhannity', 'morning', 'foxandfriends'], ['wind', 'turbines', 'alexsalmond', 'scotland', 'ugly', 'bi

## Visualization

In [25]:
# Set LLM labels as topic labels
llm_labels = [label[0][0].split("\n")[0] for label in topic_model.get_topics(full=True)["OpenAI"].values()]
topic_model.set_topic_labels(llm_labels)

In [29]:
# reduce embeddings further for visualization
reduced_embeddings_2d = UMAP(n_neighbors=15, n_components=2, min_dist=0.0, metric='cosine', verbose=True, random_state=42).fit_transform(embeddings)

UMAP(angular_rp_forest=True, metric='cosine', min_dist=0.0, n_jobs=1, random_state=42, verbose=True)
Mon Jul 28 15:13:47 2025 Construct fuzzy simplicial set
Mon Jul 28 15:13:47 2025 Finding Nearest Neighbors
Mon Jul 28 15:13:47 2025 Building RP forest with 15 trees
Mon Jul 28 15:13:48 2025 NN descent for 15 iterations
	 1  /  15
	 2  /  15
	 3  /  15
	 4  /  15
	 5  /  15
	 6  /  15
	 7  /  15
	Stopping threshold met -- exiting after 7 iterations
Mon Jul 28 15:13:55 2025 Finished Nearest Neighbor Search
Mon Jul 28 15:13:56 2025 Construct embedding


Epochs completed:   0%|            0/200 [00:00]

	completed  0  /  200 epochs
	completed  20  /  200 epochs
	completed  40  /  200 epochs
	completed  60  /  200 epochs
	completed  80  /  200 epochs
	completed  100  /  200 epochs
	completed  120  /  200 epochs
	completed  140  /  200 epochs
	completed  160  /  200 epochs
	completed  180  /  200 epochs
Mon Jul 28 15:14:20 2025 Finished embedding


In [27]:
# Visualize the topic hierarchy
fig_hierarchy = topic_model.visualize_hierarchy(custom_labels=True)

# Save the interactive plot to an HTML file
# fig_hierarchy.write_html("data/output_mergeGPT/topic_hierarchy_trump_beforeMergeGPT.html")

# Optional: Display the figure (if running in Jupyter or a script)
fig_hierarchy.show()

In [32]:
# Visualize the documents and topics with reduced embeddings
fig_docviz = topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings, custom_labels=True, hide_annotations=True, sample=5) # , custom_labels=True

# Step 2: Save the interactive plot to an HTML file
# fig_docviz.write_html("data\output_mergeGPT/docviz_trump_beforeMergeGPT.html")

# Optional: Display the figure (if running in Jupyter or a script)
fig_docviz.show()